<a href="https://colab.research.google.com/github/Talha1818/Machine-Learning-Python-Notebooks/blob/master/Check_Single_Category_Package_Name_TransData_Documents_Classification_(1).ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import os
import requests
import json
import pandas as pd
from tqdm.auto import tqdm
import glob
import os
import numpy as np
import io

In [ ]:
class credentials:
    def __init__(self, filename:str):
        self.filename = filename
    def get_credentials(self):
        with open(self.filename, 'r') as openfile:
            credentials = json.load(openfile)
        server = credentials['server']
        database = credentials['database']
        email = credentials['email']
        password = credentials['password']
        print("✅ Credentials Loaded.")
        return server, database, email, password

class Authorization:
    def __init__(self, server, email, password):
        self.server = server
        self.email = email
        self.password = password
        self.payload={'password': password,'email': email}
        self.response = requests.request("POST",  server+"authenticate/", data=self.payload)
    def check_authentication(self):
        headers = {"Authorization": ""}
        if self.response.status_code == 200:
            headers = {"Authorization": "Bearer "+json.loads(self.response.text)[0]['access_token']}
            print("✅ User Authenticated.")
            return headers
        else:
            print("❌ User Not Authenticated.")
            return headers

class Database:
    def __init__(self, server, database, headers):
        self.server = server
        self.database = database
        self.headers = headers
        self.response = requests.get(server+database, headers=self.headers)
    def get_json(self):
        if self.response.status_code == 200:
            data = self.response.json()
            print("✅ database loaded.")
            return data
        else:
            print("❌ Request failed with status code", self.response.status_code)
            return {
                "server":self.server,
                "database":self.database,
                "headers":self.headers,
                "status_code":self.response.status_cod
            }

class SaveDirectoryPdfCsv:
    def __init__(self, data, headers, directory):
        self.data = data
        self.headers = headers
        self.directory = directory
        self.df = pd.DataFrame(self.data)
        self.df['flag'] = range(self.df.shape[0])
        self.df['len'] = self.df['name'].str.split('_').apply(len)
        self.df = self.df[self.df['len']==3]

        if not os.path.exists(self.directory):
            os.makedirs(self.directory+'/PDF')
            os.makedirs(self.directory+'/CSV')
            print(f"✅ {self.directory} directory created.")
        else:
            print(f"✅ {self.directory} directory already created.")
    def save_data(self):
        for i in tqdm(self.df['flag']):
            pdf, csv, name = self.df[self.df['flag']==i][['pdf_file', 'csv_file', 'name']].values[0]            
            try:
                self.response = requests.get(pdf, headers=self.headers)
                if self.response.status_code == 200:
                    with open(f"{self.directory}/PDF/{name}.pdf", "wb") as f:
                        f.write(self.response.content) # save pdf file
                    pd.read_csv(csv).to_csv(f"{self.directory}/CSV/{name}.csv", index=False) # save csv file
                else:
                    print("Request failed with status code", self.response.status_code)
            except:
                print(f"Something went wrong with link {pdf} where flag is {i}")
        print("\n✅ All data saved in directories.")


# Credentials
cred_obj = credentials("credentials.json")
server, database, email, password = cred_obj.get_credentials()

# Authorization
auth_obj = Authorization(server=server, email=email, password=password)
headers = auth_obj.check_authentication()

# Get Database 
database_obj = Database(server=server, database=database, headers=headers)
data = database_obj.get_json()

# Save Data in Directories
dir_obj = SaveDirectoryPdfCsv(data=data, headers=headers, directory='Dataset')
dir_obj.save_data()

✅ Credentials Loaded.
✅ User Authenticated.
✅ database loaded.
✅ Dataset directory created.


  0%|          | 0/804 [00:00<?, ?it/s]


✅ All data saved in directories.


In [ ]:
FOLDER_PATH = 'Dataset'
PDF_PATH = "PDF"
CSV_PATH = "CSV"

In [ ]:
# Map the images from folder to form a DataFrame
def get_all_images_from_subdirectory_to_dataframe(path, extension='.csv'):
  configfiles = [os.path.join(dirpath, f)
      for dirpath, dirnames, files in os.walk(path)
      for f in files if f.endswith(f'{extension}')] 
  images_list = [(i.split("/")[-1].split(".")[0],i.split("/")[-1].split("_")[1],i.split("/")[-1].split("_")[2].split(".")[0], i) for i in tqdm(configfiles)]
  return images_list

In [ ]:
l = get_all_images_from_subdirectory_to_dataframe(FOLDER_PATH+"/"+CSV_PATH, extension='.csv')
csv_files = pd.DataFrame(data=l, columns=['package_name','state', 'county', 'package_path'])
csv_files.head()

  0%|          | 0/738 [00:00<?, ?it/s]

package_name state        county  \
0  217741_PA_PHILADELPHIA    PA  PHILADELPHIA   
1  218179_PA_PHILADELPHIA    PA  PHILADELPHIA   
2         612394_NJ_OCEAN    NJ         OCEAN   
3  217797_PA_PHILADELPHIA    PA  PHILADELPHIA   
4      611374_PA_DELAWARE    PA      DELAWARE   

                             package_path  
0  Dataset/CSV/217741_PA_PHILADELPHIA.csv  
1  Dataset/CSV/218179_PA_PHILADELPHIA.csv  
2         Dataset/CSV/612394_NJ_OCEAN.csv  
3  Dataset/CSV/217797_PA_PHILADELPHIA.csv  
4      Dataset/CSV/611374_PA_DELAWARE.csv

In [ ]:
l = get_all_images_from_subdirectory_to_dataframe(FOLDER_PATH+"/"+PDF_PATH, extension='.pdf')
pdf_files = pd.DataFrame(data=l, columns=['package_name','state', 'county', 'package_path'])
pdf_files.head()

  0%|          | 0/738 [00:00<?, ?it/s]

package_name state      county  \
0  217473_PA_MONTGOMERY    PA  MONTGOMERY   
1  611379_NJ_BURLINGTON    NJ  BURLINGTON   
2      116192_NJ_CAMDEN    NJ      CAMDEN   
3       217969_PA_BERKS    PA       BERKS   
4  612516_PA_MONTGOMERY    PA  MONTGOMERY   

                           package_path  
0  Dataset/PDF/217473_PA_MONTGOMERY.pdf  
1  Dataset/PDF/611379_NJ_BURLINGTON.pdf  
2      Dataset/PDF/116192_NJ_CAMDEN.pdf  
3       Dataset/PDF/217969_PA_BERKS.pdf  
4  Dataset/PDF/612516_PA_MONTGOMERY.pdf

In [ ]:
filename = 'package_with_one_category_update.xlsx'
Folder_name = '/content/drive/MyDrive/Annotation Folder'

In [ ]:
# Set the path to the Excel file
file_path = Folder_name+'/'+filename

# Create an ExcelFile object and get sheet names
xls = pd.ExcelFile(file_path)
sheet_names = xls.sheet_names
print(sheet_names)
print(len(sheet_names))


['217473_PA_MONTGOMERY', '611379_NJ_BURLINGTON', '116192_NJ_CAMDEN', '217969_PA_BERKS', '612516_PA_MONTGOMERY', '612030_NJ_CUMBERLAND', '611412_NJ_BURLINGTON', '117083_NJ_ATLANTIC', '117239_NJ_GLOUCESTER', '611456_NJ_SALEM', '612143_NJ_CAMDEN', '512289_NJ_GLOUCESTER', '612047_NJ_CAMDEN', '611669_PA_BUCKS', '217956_PA_DELAWARE', '116761_NJ_GLOUCESTER', '512305_NJ_SOMERSET', '612344_NJ_CAMDEN', '117408_NJ_CAMDEN', '117292_NJ_GLOUCESTER', '612031_PA_CHESTER', '117291_NJ_CAMDEN', '218083_PA_DELAWARE', '612034_NJ_BURLINGTON', '611928_NJ_CAMDEN', '217489_PA_PHILADELPHIA', '612052_PA_MONTGOMERY', '217840_PA_PHILADELPHIA', '611031_NJ_BURLINGTON', '117355_NJ_GLOUCESTER', '116615_NJ_CAMDEN', '612128_NJ_GLOUCESTER', '612125_NJ_BURLINGTON', '611603_NJ_CAMDEN', '116190_NJ_ATLANTIC', '117094_NJ_ATLANTIC', '611838_PA_PHILADELPHIA', '612477_NJ_GLOUCESTER', '612487_NJ_GLOUCESTER', '612104_NJ_BURLINGTON', '217207_PA_PHILADELPHIA', '612465_NJ_BURLINGTON', '117016_NJ_CAMDEN', '217784_PA_PHILADELPHIA', '51

In [ ]:
pdf_files.shape

(738, 4)

### **Check Remaining Packages**

In [ ]:
pdf_files = pdf_files[~pdf_files['package_name'].isin(sheet_names)]
pdf_files.shape

(0, 4)

In [ ]:
!pip install PyPDF2~=1.27.0

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
import PyPDF2

In [ ]:
def save_data(file, package_frequency=1):
  # Open the PDF file in read-binary mode
  with open(file, 'rb') as pdf_file:
      
      # Create a PDF reader object
      pdf_reader = PyPDF2.PdfFileReader(pdf_file)
      get_package_name = file.split("/")[-1].split(".")[0]
      try:
        get_csv_path = csv_files[csv_files['package_name']==get_package_name]['package_path'].values[0]
      except FileNotFoundError:
        print(f"This csv {get_package_name} package not found...")
      
      ########################### Read CSV FILE ###########################################
      # Read CSV file into a string
      with open(get_csv_path, 'r') as f:
          data = f.read()

      # Determine whether the file is comma-separated or tab-separated
      num_commas = data.split('\n')[0].count(',')
      num_tabs = data.split('\n')[0].count('\t')
      if num_commas > num_tabs:
          # File is comma-separated, so do nothing
          modified_data_csv = data
      else:
          # File is tab-separated, so replace tabs with commas
          modified_data_csv = data.replace('\t', ',')
      LOAD_CSV_FILE = pd.read_csv(io.StringIO(modified_data_csv))
      ############################################################################################

      dic = {}
      dic['page#'] = []
      dic['package_name'] = []
      dic['token'] = []

      ########################### Loop through each page in the PDF ##########################
      for page_num in tqdm(range(pdf_reader.getNumPages())):
        try:
          token = LOAD_CSV_FILE[LOAD_CSV_FILE['No. of Pages']==page_num+1]['Token'].values.tolist()[0]
          # print(page_num+1, "==>", token)
          dic['page#'].append(page_num+1)
          dic['package_name'].append(get_package_name)
          dic['token'].append(token)
        except:
          print(f"Issue in file {get_package_name} PAGE### ({page_num+1})")
          dic['page#'].append('')
          dic['package_name'].append('')
          dic['token'].append('')
      
      ###########################################################################################

      ################################### Read Token Meaning File ##########################

      df_token = pd.read_csv("/content/drive/MyDrive/Annotation Folder/lender_docs_token.csv")

      ########################################################################################
      
      ############################### Creating A DataFrame ###################################
      df = pd.DataFrame(dic)
      counts = df['token'].value_counts()
      result = counts[counts == package_frequency].to_frame().reset_index().rename(
          columns={'index': 'token', 'token': 'frequency'})
      result = result.sort_values(by='token')
      result['package_name'] = get_package_name
      get_token = result['token'].values.tolist()
      get_meaning = df_token[df_token['Token'].isin(get_token)].sort_values(by='Token')['Meaning'].values.tolist()

      result['Meaning'] = get_meaning + ['']*(abs(len(get_token)-len(get_meaning)))
      result = result.reset_index(drop=True)

      ###########################################################################
      return result[['package_name', 'Meaning', 'token', 'frequency']]

In [ ]:
# save_data(file)

In [ ]:
# Create an ExcelWriter object
with pd.ExcelWriter(Folder_name+'/'+filename, mode='a') as writer:
  for FILE in tqdm(pdf_files['package_path']):
    get_package_name = FILE.split("/")[-1].split(".")[0]
    print(get_package_name)
    DATA = save_data(FILE)
    DATA.to_excel(writer, sheet_name=get_package_name, index=False)

  0%|          | 0/723 [00:00<?, ?it/s]

116761_NJ_GLOUCESTER


  0%|          | 0/109 [00:00<?, ?it/s]

512305_NJ_SOMERSET


  0%|          | 0/83 [00:00<?, ?it/s]

...

  0%|          | 0/150 [00:00<?, ?it/s]

611434_PA_PHILADELPHIA


  0%|          | 0/128 [00:00<?, ?it/s]

612408_PA_MONTGOMERY


  0%|          | 0/142 [00:00<?, ?it/s]

In [ ]:
import smtplib
from email.mime.multipart import MIMEMultipart
from email.mime.text import MIMEText
from email.mime.base import MIMEBase
from email import encoders

# Set up email parameters
email_user = "muhammadtalha1818@gmail.com"
email_password = "ikqefajjctpsmdyi"
email_send = "meet.ahmad247@gmail.com"
subject = "One Category CSV file attachment"

body = "Please find the attached CSV file."

# Create a multipart message object and set headers
msg = MIMEMultipart()
msg['From'] = email_user
msg['To'] = email_send
msg['Subject'] = subject

# Attach body to message
msg.attach(MIMEText(body, 'plain'))

# Open the file in bynary
attachment = open(Folder_name+'/'+filename, "rb")

# Create a base64 encoded attachment object
part = MIMEBase('application', 'octet-stream')
part.set_payload((attachment).read())
encoders.encode_base64(part)
part.add_header('Content-Disposition', "attachment; filename= %s" % filename)

# Attach the file to the message object and send the email
msg.attach(part)
text = msg.as_string()
server = smtplib.SMTP('smtp.gmail.com', 587)
server.starttls()
server.login(email_user, email_password)

server.sendmail(email_user, email_send, text)
server.quit()
print("S E N T !!!!")

S E N T !!!!
